# 3D Plotting 🌪️

In [1]:
import numpy as np
import torch
import plotly.graph_objects as go
from plotly.colors import qualitative
import warnings
from optimizers.adam_clara import Adam_CLARA
from optimizers.sgd_clara import SGD_CLARA

----
### Mathematical Functions 🧮

In [2]:
def rosenbrock(x):
    a, b = 1, 100
    return (a - x[0])**2 + b*(x[1] - x[0]**2)**2

def rosenbrock_torch(x):
    a, b = 1, 100
    return (a - x[0])**2 + b*(x[1] - x[0]**2)**2


def himmelblau(x):
    return (x[0]**2 + x[1] - 11)**2 + (x[0] + x[1]**2 - 7)**2

def himmelblau_torch(x):
    return (x[0]**2 + x[1] - 11)**2 + (x[0] + x[1]**2 - 7)**2


def beale(x):
    return ((1.5 - x[0] + x[0]*x[1])**2 +
            (2.25 - x[0] + x[0]*x[1]**2)**2 +
            (2.625 - x[0] + x[0]*x[1]**3)**2)

def beale_torch(x):
    return ((1.5 - x[0] + x[0]*x[1])**2 +
            (2.25 - x[0] + x[0]*x[1]**2)**2 +
            (2.625 - x[0] + x[0]*x[1]**3)**2)
    
    
def eggholder(x):
    return (-(x[1]+47)*np.sin(np.sqrt(abs(x[0]/2 + (x[1]+47)))) - 
            x[0]*np.sin(np.sqrt(abs(x[0] - (x[1]+47)))))

def eggholder_torch(x):
    term1 = -(x[1]+47)*torch.sin(torch.sqrt(torch.abs(x[0]/2 + (x[1]+47))))
    term2 = -x[0]*torch.sin(torch.sqrt(torch.abs(x[0] - (x[1]+47))))
    return term1 + term2


def three_hump_camel(x):
    return 2*x[0]**2 - 1.05*x[0]**4 + (x[0]**6)/6 + x[0]*x[1] + x[1]**2

def three_hump_camel_torch(x):
    return (2*x[0]**2 - 1.05*x[0]**4 + (x[0]**6)/6 + x[0]*x[1] + x[1]**2)


def ackley(x):
    x0, x1 = x[0], x[1]
    part1 = -20*np.exp(-0.2*np.sqrt(0.5*(x0**2 + x1**2)))
    part2 = -np.exp(0.5*(np.cos(2*np.pi*x0) + np.cos(2*np.pi*x1)))
    return part1 + part2 + np.e + 20

def ackley_torch(x):
    part1 = -20*torch.exp(-0.2*torch.sqrt(0.5*(x[0]**2 + x[1]**2)))
    part2 = -torch.exp(0.5*(torch.cos(2*torch.pi*x[0]) + torch.cos(2*torch.pi*x[1])))
    return part1 + part2 + torch.exp(torch.tensor(1.0)) + 20

----
### Helper Functions 🛠️

In [3]:
def to_torch_tensor(x, device='cpu'):
    return torch.tensor(x, dtype=torch.float32, device=device, requires_grad=True)


def numpy_func_wrapper(func):
    """Return a function that converts torch.Tensor to numpy and applies func"""
    def f(x_torch):
        x_np = x_torch.detach().cpu().numpy()
        return func(x_np)
    return f

# %%
def get_func_and_torch(name):
    funcs_np = {
        "rosenbrock": rosenbrock,
        "himmelblau": himmelblau,
        "beale": beale,
        "eggholder": eggholder,
        "three_hump_camel": three_hump_camel,
        "ackley": ackley,
    }
    funcs_torch = {
        "rosenbrock": rosenbrock_torch,
        "himmelblau": himmelblau_torch,
        "beale": beale_torch,
        "eggholder": eggholder_torch,
        "three_hump_camel": three_hump_camel_torch,
        "ackley": ackley_torch,
    }
    return funcs_np[name], funcs_torch[name]

----
### Plot- und Optimierungsmethode 📊

In [ ]:
def optimize_and_plot(
    func_np, func_torch, global_optimum, 
    optimizers, 
    start_points,
    bounds=[-2, 2], 
    steps_dict=None,
    lr_dict=None,
    gradient_clip=None,
    device='cpu',
    func_name=None
):
    # Surface grid
    x_vals = y_vals = np.linspace(bounds[0], bounds[1], 200)
    X, Y = np.meshgrid(x_vals, y_vals)
    Z = np.zeros_like(X)

    # Compute surface
    for i in range(X.shape[0]):
        for j in range(X.shape[1]):
            try:
                val = func_np(np.array([X[i, j], Y[i, j]]))
                if not np.isfinite(val):  # NaN or inf
                    val = np.nan
                Z[i, j] = val
            except Exception:
                Z[i, j] = np.nan

    # Diagnose before Clipping
    print(f"[{func_name}] Z stats before clipping: min={np.nanmin(Z):.2e}, max={np.nanmax(Z):.2e}")

    # Remove non-finite values
    Z_finite = Z[np.isfinite(Z)]

    # Clip numerically extreme values
    Z_finite = Z_finite[(Z_finite > -1e3) & (Z_finite < 1e3)]

    if len(Z_finite) == 0:
        raise ValueError("Z values are too extreme or all non-finite.")

    zmin, zmax = np.percentile(Z_finite, [2, 98])
    Z = np.clip(Z, zmin, zmax)

    print(f"[{func_name}] Z range after clipping: {zmin:.2f} to {zmax:.2f}")

    # Optional: logarithmic Transformation
    # Z = np.log1p(Z - Z.min() + 1e-8)

    # Optimization paths
    paths = {}
    color_cycle = qualitative.Plotly
    color_list = list(color_cycle)
    color_map = {}

    for idx, (name, OptimizerClass) in enumerate(optimizers.items()):
        lr = lr_dict.get(name, 0.01) if lr_dict else 0.01
        steps = steps_dict.get(name, 50) if steps_dict else 50
        start = start_points[name]

        x_torch = torch.tensor(start, dtype=torch.float32, device=device, requires_grad=True)
        optimizer = OptimizerClass([x_torch], lr=lr)
        path = [x_torch.detach().cpu().clone().numpy()]

        for step_idx in range(steps):
            optimizer.zero_grad()
            val = func_torch(x_torch)
            val.backward()

            if gradient_clip:
                # Clip gradients for stability
                torch.nn.utils.clip_grad_norm_([x_torch], max_norm=gradient_clip)

            optimizer.step()

            # Clip positions to bounds after step to avoid divergence
            with torch.no_grad():
                x_torch[:] = torch.clamp(x_torch, bounds[0], bounds[1])

            # Log divergence if any coordinate becomes too large
            if not torch.isfinite(x_torch).all() or (x_torch.abs() > 1e3).any():
                print(f"⚠️ Divergence detected in optimizer '{name}' at step {step_idx}: {x_torch.detach().cpu().numpy()}")
                break

            # Store path
            path.append(x_torch.detach().cpu().clone().numpy())


        paths[name] = np.array(path)
        color_map[name] = color_list[idx % len(color_list)]

    # Plotly figure
    fig = go.Figure()

    fig.add_trace(go.Surface(
        x=X, y=Y, z=Z,
        colorscale='Viridis',
        opacity=0.9,
        name='Loss Surface',
        showscale=True,
        colorbar=dict(title='Loss')
    ))

    for name, path in paths.items():
        try:
            Z_path = [np.clip(func_np(p), zmin, zmax) for p in path]
        except Exception as e:
            warnings.warn(f"Failed to evaluate path for {name}: {e}")
            Z_path = [zmax for _ in path]
        
        fig.add_trace(go.Scatter3d(
            x=path[:, 0], y=path[:, 1], z=Z_path,
            mode='lines+markers',
            line=dict(color=color_map[name], width=4),
            marker=dict(size=3),
            name=f'{name} Path'
        ))

    fig.add_trace(go.Scatter3d(
        x=[global_optimum[0]],
        y=[global_optimum[1]],
        z=[np.clip(func_np(global_optimum), zmin, zmax)],
        mode='markers+text',
        marker=dict(size=8, color='purple'),
        text=["Global Optimum"],
        textposition='top center',
        name='Global Optimum'
    ))

    fig.update_layout(
        title=f"Optimization Paths on Objective Surface: {func_name}",
        scene=dict(
            xaxis_title="x",
            yaxis_title="y",
            zaxis_title="f(x, y)",
            zaxis=dict(range=[zmin, zmax]),
            camera=dict(eye=dict(x=1.5, y=1.5, z=1.0))
        ),
        width=950,
        height=650,
        margin=dict(l=0, r=0, t=50, b=0),
        font=dict(family="Arial", size=14),
        legend=dict(x=0.8, y=0.95)
    )

    fig.show()


-----
### Main Function 🚀

In [ ]:
if __name__ == "__main__":
    # Optimizer Klassen
    optimizers = {
        'SGD': torch.optim.SGD,
        'ADAM': torch.optim.Adam,
        'Adam_CLARA': Adam_CLARA,
        'SGD_CLARA': SGD_CLARA,
    }

    # Funktion-spezifische Startpunkte
    per_func_startpoints = {
        "rosenbrock": {
            'SGD': np.array([-1.5, 1.5]),
            'ADAM': np.array([1.5, -1.5]),
            'Adam_CLARA': np.array([-1.0, 1.0]),
            'SGD_CLARA': np.array([1.0, -1.0]),
        },
        "himmelblau": {
            'SGD': np.array([-4.0, 4.0]),
            'ADAM': np.array([4.0, -4.0]),
            'Adam_CLARA': np.array([-3.0, 3.0]),
            'SGD_CLARA': np.array([3.0, -3.0]),
        },
        "beale": {
            'SGD': np.array([1.0, 1.0]),
            'ADAM': np.array([2.5, 2.0]),
            'Adam_CLARA': np.array([-1.0, 1.0]),
            'SGD_CLARA': np.array([1.5, -1.5]),
        },
        "eggholder": {
            'SGD': np.array([500, 300]),
            'ADAM': np.array([300, 500]),
            'Adam_CLARA': np.array([400, 400]),
            'SGD_CLARA': np.array([450, 450]),
        },
        "three_hump_camel": {
            'SGD': np.array([1.0, 1.0]),
            'ADAM': np.array([-1.0, -1.0]),
            'Adam_CLARA': np.array([1.5, -1.5]),
            'SGD_CLARA': np.array([-1.5, 1.5]),
        },
        "ackley": {
            'SGD': np.array([2.0, 2.0]),
            'ADAM': np.array([-2.0, -2.0]),
            'Adam_CLARA': np.array([2.5, -2.5]),
            'SGD_CLARA': np.array([-2.5, 2.5]),
        }
    }

    # Schrittanzahl pro Optimizer
    steps_dict = {
        'SGD': 100,
        'ADAM': 80,
        'Adam_CLARA': 80,
        'SGD_CLARA': 100,
    }

    # Lernraten pro Optimizer
    lr_dict = {
        'SGD': 0.01,
        'ADAM': 0.005,
        'Adam_CLARA': 0.005,
        'SGD_CLARA': 0.01,
    }

    # Globales Optimum
    global_optima = {
        "rosenbrock": np.array([1.0, 1.0]),
        "himmelblau": np.array([3.0, 2.0]),
        "beale": np.array([3.0, 0.5]),
        "eggholder": np.array([512.0, 404.2319]),
        "three_hump_camel": np.array([0.0, 0.0]),
        "ackley": np.array([0.0, 0.0]),
    }

    # Plotbereiche pro Funktion
    func_bounds = {
        "rosenbrock": [-2, 2],
        "himmelblau": [-6, 6],
        "beale": [-4.5, 4.5],
        "eggholder": [0, 600],
        "three_hump_camel": [-3, 3],
        "ackley": [-5, 5],
    }

    # Liste der Funktionen
    func_names = list(global_optima.keys())

    for func_name in func_names:
        print(f"\n--- Generating plot for: {func_name} ---")
        func_np, func_torch = get_func_and_torch(func_name)
        optimize_and_plot(
            func_np=func_np,
            func_torch=func_torch,
            global_optimum=global_optima[func_name],
            optimizers=optimizers,
            start_points=per_func_startpoints[func_name],
            bounds=func_bounds[func_name],
            steps_dict=steps_dict,
            lr_dict=lr_dict,
            gradient_clip=5.0,  
            func_name=func_name  
        )



--- Generating plot for: rosenbrock ---
[rosenbrock] Z stats before clipping: min=2.53e-03, max=3.61e+03
[rosenbrock] Z range after clipping: 1.18 to 912.60



--- Generating plot for: himmelblau ---
[himmelblau] Z stats before clipping: min=2.03e-03, max=2.19e+03
[himmelblau] Z range after clipping: 6.70 to 882.04



--- Generating plot for: beale ---
[beale] Z stats before clipping: min=1.51e-03, max=1.82e+05
[beale] Z range after clipping: 0.85 to 878.40



--- Generating plot for: eggholder ---
[eggholder] Z stats before clipping: min=-9.93e+02, max=1.18e+03
[eggholder] Z range after clipping: -775.40 to 699.43



--- Generating plot for: three_hump_camel ---
[three_hump_camel] Z stats before clipping: min=4.54e-04, max=7.25e+01
[three_hump_camel] Z range after clipping: 0.30 to 52.18



--- Generating plot for: ackley ---
[ackley] Z stats before clipping: min=1.34e-01, max=1.43e+01
[ackley] Z range after clipping: 3.66 to 13.63
